# Phi-4-multimodal simple demo

Make sure that you must install `gradio, soundfile, and pillow`.

- `pip install gradio transformers torch soundfile pillow`
- Retrieved from https://www.datacamp.com/tutorial/phi-4-multimodal

In [ ]:
import gradio as gr
import torch
import requests
import io
import os
import soundfile as sf
from PIL import Image
from datasets import load_dataset
from transformers import AutoModelForCausalLM, AutoProcessor, GenerationConfig


max_new_tokens = 256
orig_model_path = "microsoft/Phi-4-multimodal-instruct"
ft_model_path = "daekeun-ml/Phi-4-multimodal-finetune-ko-speech"
generation_config = GenerationConfig.from_pretrained(ft_model_path, 'generation_config.json')
processor = AutoProcessor.from_pretrained(orig_model_path, trust_remote_code=True)
model = AutoModelForCausalLM.from_pretrained(
    ft_model_path,
    trust_remote_code=True,
    torch_dtype='auto',
    _attn_implementation='flash_attention_2',
).cuda()

user_prompt = '<|user|>'
assistant_prompt = '<|assistant|>'
prompt_suffix = '<|end|>'

In [ ]:
def clean_response(response, instruction_keywords):
    """Removes the prompt text dynamically based on instruction keywords."""
    for keyword in instruction_keywords:
        if response.lower().startswith(keyword.lower()):
            response = response[len(keyword):].strip()
    return response

# task prompt is from technical report
asr_prompt = f'{user_prompt}<|audio_1|>Transcribe the audio clip into text.{prompt_suffix}{assistant_prompt}'
ast_ko_prompt = f'{user_prompt}<|audio_1|>Translate the audio to Korean.{prompt_suffix}{assistant_prompt}'
ast_cot_ko_prompt = f'{user_prompt}<|audio_1|>Transcribe the audio to text, and then translate the audio to Korean. Use <sep> as a separator between the original transcript and the translation.{prompt_suffix}{assistant_prompt}'
ast_en_prompt = f'{user_prompt}<|audio_1|>Translate the audio to English.{prompt_suffix}{assistant_prompt}'
ast_cot_en_prompt = f'{user_prompt}<|audio_1|>Transcribe the audio to text, and then translate the audio to English. Use <sep> as a separator between the original transcript and the translation.{prompt_suffix}{assistant_prompt}'

def process_input(file, input_type, question):
    user_prompt = "<|user|>"
    assistant_prompt = "<|assistant|>"
    prompt_suffix = "<|end|>"
    
    if input_type == "Image":
        prompt= f'{user_prompt}<|image_1|>{question}{prompt_suffix}{assistant_prompt}'
        image = Image.open(file)
        inputs = processor(text=prompt, images=image, return_tensors='pt').to(model.device)
    elif input_type == "Audio":
        prompt= f'{user_prompt}<|audio_1|>{question}{prompt_suffix}{assistant_prompt}'
        audio, samplerate = sf.read(file)
        inputs = processor(text=prompt, audios=[(audio, samplerate)], return_tensors='pt').to(model.device)
    elif input_type == "Text":
        prompt = f'{user_prompt}{question} "{file}"{prompt_suffix}{assistant_prompt}'
        inputs = processor(text=prompt, return_tensors='pt').to(model.device)
    else:
        return "Invalid input type"    
    
    generate_ids = model.generate(**inputs, max_new_tokens=1000, generation_config=generation_config)
    response = processor.batch_decode(generate_ids, skip_special_tokens=True)[0]
    return clean_response(response, [question])

def process_text_translate(text, target_language):
    prompt = f'Transcribe the audio to text, and then Translate the following text to {target_language}: "{text}"'
    return process_input(text, "Text", prompt)
def process_text_grammar(text):
    prompt = f'Check the grammar and provide corrections if needed for the following text: "{text}"'
    return process_input(text, "Text", prompt)

def gradio_interface():
    with gr.Blocks() as demo:
        gr.Markdown("# Phi 4 Powered - Multimodal Language Tutor")        
        with gr.Tab("Text-Based Learning"):
            text_input = gr.Textbox(label="Enter Text")
            language_input = gr.Textbox(label="Target Language", value="Korean")
            text_output = gr.Textbox(label="Response")
            text_translate_btn = gr.Button("Translate")
            text_grammar_btn = gr.Button("Check Grammar")
            text_clear_btn = gr.Button("Clear")
            text_translate_btn.click(process_text_translate, inputs=[text_input, language_input], outputs=text_output)
            text_grammar_btn.click(process_text_grammar, inputs=[text_input], outputs=text_output)
            text_clear_btn.click(lambda: ("", "", ""), outputs=[text_input, language_input, text_output])        
        with gr.Tab("Image-Based Learning"):
            image_input = gr.Image(type="filepath", label="Upload Image")
            language_input_image = gr.Textbox(label="Target Language for Translation", value="English")
            image_output = gr.Textbox(label="Response")
            image_clear_btn = gr.Button("Clear")
            image_translate_btn = gr.Button("Translate Text in Image")
            image_summarize_btn = gr.Button("Summarize Image")
            image_translate_btn.click(process_input, inputs=[image_input, gr.Textbox(value="Image", visible=False), gr.Textbox(value="Extract and translate text", visible=False)], outputs=image_output)
            image_summarize_btn.click(process_input, inputs=[image_input, gr.Textbox(value="Image", visible=False), gr.Textbox(value="Summarize this image", visible=False)], outputs=image_output)
            image_clear_btn.click(lambda: (None, "", ""), outputs=[image_input, language_input_image, image_output])
        with gr.Tab("Audio-Based Learning"):
            audio_input = gr.Audio(type="filepath", label="Upload Audio")
            language_input_audio = gr.Textbox(label="Target Language for Translation", value="English")
            transcript_output = gr.Textbox(label="Transcribed Text")
            translated_output = gr.Textbox(label="Translated Text")
            audio_clear_btn = gr.Button("Clear")
            audio_transcribe_btn = gr.Button("Transcribe & Translate")
            audio_transcribe_btn.click(process_input, inputs=[audio_input, gr.Textbox(value="Audio", visible=False), gr.Textbox(value="Transcribe this audio", visible=False)], outputs=transcript_output)
            audio_transcribe_btn.click(process_input, inputs=[audio_input, gr.Textbox(value="Audio", visible=False), language_input_audio], outputs=translated_output)
            audio_clear_btn.click(lambda: (None, "", "", ""), outputs=[audio_input, language_input_audio, transcript_output, translated_output])        
        demo.launch(debug=True, share=True)

if __name__ == "__main__":
    gradio_interface()